In [3]:
!python settings.py

Using device: cuda


In [4]:
import os
import zipfile
import requests
import pandas as pd

In [5]:
# Download the dataset
url      = 'https://huggingface.co/datasets/tmnam20/BKAI-Legal-Retrieval/resolve/main/archive.zip'
zip_path = 'data/original/archive.zip'

response = requests.get(url)
with open(zip_path, 'wb') as f:
    f.write(response.content)

with zipfile.ZipFile(zip_path, 'r') as zip_ref:
    zip_ref.extractall('data/original')
    
os.remove(zip_path)

In [6]:
corpus_data = pd.read_csv('data/original/corpus.csv')
train_split = pd.read_csv('data/original/train_split.csv')
test_split  = pd.read_csv('data/original/val_split.csv')

print(f"Train split data: {len(train_split)}")
print(f"Test split data : {len(test_split)}")

Train split data: 89592
Test split data : 29864


In [7]:
corpus_data.head()

text  cid
0  Thông tư này hướng dẫn tuần tra, canh gác bảo ...    0
1  1. Hàng năm trước mùa mưa, lũ, Ủy ban nhân dân...    1
2  Tiêu chuẩn của các thành viên thuộc lực lượng ...    2
3  Nhiệm vụ của lực lượng tuần tra, canh gác đê\n...    3
4  Phù hiệu của lực lượng tuần tra, canh gác đê\n...    4

In [8]:
# 'cid' column: '[1 2 3]'
train_split['cid'] = train_split['cid'].apply(lambda x: [int(i) for i in x[1:-1].split()])
test_split['cid']  = test_split['cid'].apply(lambda x: [int(i) for i in x[1:-1].split()])


# Mapping from corpus 
mapping = dict(zip(corpus_data['cid'], corpus_data['text']))

def get_context_list(cid_list):
    return [mapping[cid] for cid in cid_list if cid in mapping]

train_split['context_list'] = train_split['cid'].apply(get_context_list)
test_split['context_list']  = test_split['cid'].apply(get_context_list)

train_split.head()

question  \
0  Liên đoàn Luật sư Việt Nam là tổ chức xã hội –...   
1  Tên hợp tác xã bị rơi vào trường hợp cấm thì c...   
2  Tài xế lái xe ô tô khách 50 chỗ ngồi bao lâu t...   
3  Các bước chuẩn bị thủ thuật bó bột Cravate sẽ ...   
4  Viên chức Hộ sinh hạng 4 có những nhiệm vụ gì ...   

                                             context             cid     qid  \
0  ['“Điều 2. Địa vị pháp lý của Liên đoàn Luật s...        [142820]   72600   
1  ['Tên hợp tác xã, liên hiệp hợp tác xã\n1. Tên...  [27817, 72117]  147562   
2  ['"1. Sử dụng lái xe bảo đảm sức khỏe theo tiê...  [33215, 56201]  142107   
3  ['BỘT CRAVATE\n...\nIV. CHUẨN BỊ\n1. Người thự...        [148158]   77353   
4  ['Hộ sinh hạng IV - Mã số: V.08.06.16\n1. Nhiệ...        [188132]  113090   

                                        context_list  
0  [“Điều 2. Địa vị pháp lý của Liên đoàn Luật sư...  
1  ["Điều 7. Tên hợp tác xã, liên hiệp hợp tác xã...  
2  ["1. Sử dụng lái xe bảo đảm sức khỏe theo tiêu...  
3  [BỘT CRAVATE\n...\nIV. CHUẨN BỊ\n1. Người thực...  
4  [Hộ sinh hạng IV - Mã số: V.08.06.16\n1. Nhiệm...

In [9]:
# Debug
print(
    len(train_split[train_split['context_list'].apply(len) != train_split['cid'].apply(len)]),
    
    len(
        train_split[
            (train_split['context_list'].apply(len) != train_split['cid'].apply(len)) &
            (train_split['context_list'].apply(len) != 0)
        ]
    ),
    
    len(
        train_split[
            (train_split['context_list'].apply(len) != train_split['cid'].apply(len)) &
            (train_split['context_list'].apply(len) == 0)
        ]
    )
)

for col in train_split.columns:
    print(col, type(train_split[col][0]))

430 99 331
question <class 'str'>
context <class 'str'>
cid <class 'list'>
qid <class 'numpy.int64'>
context_list <class 'list'>


In [10]:
# Drop invalid data
train_data = train_split.loc[
    ~(train_split['context_list'].apply(len) != train_split['cid'].apply(len)), 
    ['question', 'context_list', 'qid', 'cid']
]

test_data = test_split.loc[
    ~(test_split['context_list'].apply(len) != test_split['cid'].apply(len)), 
    ['question', 'context_list', 'qid', 'cid']
]

In [11]:
# Save the processed data to parquet files
corpus_data.to_parquet('data/processed/corpus_data.parquet', index=False)
train_data.to_parquet('data/processed/train_data.parquet', index=False)
test_data.to_parquet('data/processed/test_data.parquet', index=False)

print(f"Train data saved: {len(train_data)}")
print(f"Test data saved : {len(test_data)}")

Train data saved: 89162
Test data saved : 29723


In [12]:
# # Get demo data
# os.makedirs('data/demo', exist_ok=True)

# demo_corpus_data = corpus_data.sample(10, random_state=42).reset_index(drop=True)
# demo_train_data  = train_data.sample(10, random_state=42).reset_index(drop=True)
# demo_test_data   = test_data.sample(10, random_state=42).reset_index(drop=True)

# demo_corpus_data.to_csv('data/demo/demo_corpus_data.csv', index=False)
# demo_train_data.to_csv('data/demo/demo_train_data.csv', index=False)
# demo_test_data.to_csv('data/demo/demo_test_data.csv', index=False)